##DYNA : Integrating Planning, Acting and Learning

###Enviroment

For this assignment I selected the Frozen Lake environment from OpenAi gym. The agent controls the movement of a character in a grid world. Some tiles of the grid are walkable, and others lead to the agent falling into the water. Additionally, the movement direction of the agent is uncertain and only partially depends on the chosen direction, i.e., the environment is stochastic. The agent recieves a reward of 1 if if reaches the goal and 0 otherwise.

'Solving' this environment is defined as getting average reward of 0.78 over 100 consecutive trials.



In [4]:
import gym
import numpy as np

# slipperly lake, so actions not deterministic!
env = gym.make('FrozenLake-v0')

env.render()

next_s, r, is_end, inf = env.step(action=0)
print(next_s, r, is_end, inf)
env.render()

INFO:gym.envs.registration:Making new env: FrozenLake-v0
[2017-02-25 18:03:15,175] Making new env: FrozenLake-v0


SFFF
FHFH
FFFH
HFFG

(0, 0.0, False, {'prob': 0.3333333333333333})
SFFF
FHFH
FFFH
HFFG
  (Left)


I first show that simple standard direct RL methods like Q-learning and SARSA are able to solve this task. In order to make the task more interesting wemodify the reward structure. In order to encourage the RL agent to reach the goal faster, a reward of -1 is added for every timestep that passes without reaching the goal. The reward for reaching the goal is amplified from 1 to 100.


Next we analyse the performance of expected SARSA and double-Q learning on this problem. Finally we see if adding planning capabilities is able to improve the agents performance.
It is worth noting that intuitively one would not expect planning to help. This is because the environment is stochastic

###Q-Learning

In [2]:
import qlearning

In [7]:
env = gym.make("FrozenLake-v0")
Q=qlearning.train(env,planning=False)

INFO:gym.envs.registration:Making new env: FrozenLake-v0
[2017-02-25 13:19:55,141] Making new env: FrozenLake-v0


Episode 0 finished after 6 timesteps with r=0.0. Running score: 0.0
Episode 1 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 2 finished after 8 timesteps with r=0.0. Running score: 0.0
Episode 3 finished after 2 timesteps with r=0.0. Running score: 0.0
Episode 4 finished after 14 timesteps with r=1.0. Running score: 0.2
Episode 5 finished after 11 timesteps with r=0.0. Running score: 0.166666666667
Episode 6 finished after 2 timesteps with r=0.0. Running score: 0.142857142857
Episode 7 finished after 7 timesteps with r=0.0. Running score: 0.125
Episode 8 finished after 9 timesteps with r=0.0. Running score: 0.111111111111
Episode 9 finished after 4 timesteps with r=0.0. Running score: 0.1
Episode 10 finished after 9 timesteps with r=0.0. Running score: 0.0909090909091
Episode 11 finished after 17 timesteps with r=0.0. Running score: 0.0833333333333
Episode 12 finished after 8 timesteps with r=0.0. Running score: 0.0769230769231
Episode 13 finished after 18 timesteps 

Evaluate the learned Q-table for 1000 episodes

In [8]:
env = gym.make("FrozenLake-v0")
qlearning.evaluate(env,Q)

INFO:gym.envs.registration:Making new env: FrozenLake-v0
[2017-02-25 13:20:28,281] Making new env: FrozenLake-v0


1000 episodes finished in an average of 47.5592803955. Running score: 0.9


###SARSA

The performance of SARSA is very similar to Q-learning, perhaps slightly better. On average SARSA took more steps to reach the goal than Q-learning over multiple runs

In [3]:
import sarsa

In [4]:
Q = sarsa.train(env,planning=False)

Episode 0 finished after 8 timesteps with r=0.0. Running score: 0.0
Episode 1 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 2 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 3 finished after 29 timesteps with r=0.0. Running score: 0.0
Episode 4 finished after 1 timesteps with r=0.0. Running score: 0.0
Episode 5 finished after 21 timesteps with r=0.0. Running score: 0.0
Episode 6 finished after 3 timesteps with r=0.0. Running score: 0.0
Episode 7 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 8 finished after 6 timesteps with r=0.0. Running score: 0.0
Episode 9 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 10 finished after 8 timesteps with r=0.0. Running score: 0.0
Episode 11 finished after 16 timesteps with r=0.0. Running score: 0.0
Episode 12 finished after 8 timesteps with r=0.0. Running score: 0.0
Episode 13 finished after 19 timesteps with r=0.0. Running score: 0.0
Episode 14 finished after 16 timesteps w

In [5]:
sarsa.evaluate(env,Q)

1000 episodes finished in an average of 46.9476242065. Running score: 0.81


We see after 10000 episondes the running average reward is 0.8 (approx) at which point this environment may be considered solved. Thus q-learning is able to perform quite well on this task. In order to evaluate the policy being learned, we play out 1000 episodes using the learned Q-table.

###Planning

Planning can typically be used in order to improve the policy by combining direct RL-methods or learning methods with simulated rather than real experience. This involves a model learning stage. The simplest type of model is deterministic. Here we experiment with DYNA-Q based planning agensts. Note that as the environment is stochastic, using a determistic model can be expected to hurt performance, as we show through experimentation. 

For all the experiments in this notebook we used 15 planning steps. We experimented with a larger number of steps, however the gains were marginal as compared to the increased computational complexity.

In [ ]:
def plan(Q,lr,y,model_nextS,model_nextR,plan_steps=15):
    
    vis_before = np.nonzero(model_nextS)
    pstates = list(set(vis_before[0]))

    psteps=0        
    
    while psteps<=plan_steps-1:

        #select a state at random from previous states
        if pstates:
            rstate = random.sample(pstates,1)
            rstate = rstate[0]
        else:
            rstate=0
        #find previously sampled actions
        pacts = np.nonzero(model_nextS[rstate,:])
        if pacts[0].any():
            ract = random.sample(pacts[0],1)
            ract = ract[0]
        else:
            ract=0

        #simulate experience from model
        r_hat = (model_nextR[rstate,ract]).astype('int32')
        s_hat = (model_nextS[rstate,ract]).astype('int32')
    
        #use Q-learning for planning
        Q[rstate,ract] = Q[rstate,ract] + lr*(r_hat + y*np.max(Q[s_hat,:]) - Q[rstate,ract])
        psteps+=1

    return Q   

We now traing Q-learning with 15 planning steps, that also uses Q-learning on simulated experience.

In [3]:
env = gym.make("FrozenLake-v0")
Q=qlearning.train(env,planning=True)

INFO:gym.envs.registration:Making new env: FrozenLake-v0
[2017-02-25 13:38:10,405] Making new env: FrozenLake-v0


Episode 0 finished after 6 timesteps with r=0.0. Running score: 0.0
Episode 1 finished after 2 timesteps with r=0.0. Running score: 0.0
Episode 2 finished after 7 timesteps with r=0.0. Running score: 0.0
Episode 3 finished after 13 timesteps with r=0.0. Running score: 0.0
Episode 4 finished after 24 timesteps with r=0.0. Running score: 0.0
Episode 5 finished after 7 timesteps with r=0.0. Running score: 0.0
Episode 6 finished after 3 timesteps with r=0.0. Running score: 0.0
Episode 7 finished after 6 timesteps with r=0.0. Running score: 0.0
Episode 8 finished after 6 timesteps with r=0.0. Running score: 0.0
Episode 9 finished after 15 timesteps with r=0.0. Running score: 0.0
Episode 10 finished after 4 timesteps with r=0.0. Running score: 0.0
Episode 11 finished after 24 timesteps with r=0.0. Running score: 0.0
Episode 12 finished after 2 timesteps with r=0.0. Running score: 0.0
Episode 13 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 14 finished after 2 timesteps wi

In [4]:
qlearning.evaluate(env,Q)

1000 episodes finished in an average of 26.619354248. Running score: 0.35


As expected, we see that the planning agent doesn't perform as well as SARSA or Q-learning in terms of the average achieved reward. Interestingly, althought the DYNA agent reaches the goal less often it does so in a much smaller number of steps. We observe this trend over multiple runs of the algorithm.

In order to better understand how the stochasticity of the environment affects learning and planning agents, we also attempt to solve the FrozenLake-v0 environment using expected SARSA and Double Q-learning. Intuitively expected SARSA should also suffer due to the enviromental stochasticity.

### Expected SARSA

In [1]:
import esarsa

In [5]:
#env = gym.make("FrozenLake-v0")
Q = esarsa.train(env,planning=False)

Episode 0 finished after 11 timesteps with r=0.0. Running score: 0.0
Episode 1 finished after 8 timesteps with r=0.0. Running score: 0.0
Episode 2 finished after 16 timesteps with r=0.0. Running score: 0.0
Episode 3 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 4 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 5 finished after 3 timesteps with r=0.0. Running score: 0.0
Episode 6 finished after 2 timesteps with r=0.0. Running score: 0.0
Episode 7 finished after 20 timesteps with r=0.0. Running score: 0.0
Episode 8 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 9 finished after 18 timesteps with r=0.0. Running score: 0.0
Episode 10 finished after 9 timesteps with r=0.0. Running score: 0.0
Episode 11 finished after 31 timesteps with r=0.0. Running score: 0.0
Episode 12 finished after 44 timesteps with r=0.0. Running score: 0.0
Episode 13 finished after 19 timesteps with r=0.0. Running score: 0.0
Episode 14 finished after 10 timestep

In [6]:
esarsa.evaluate(env,Q)

1000 episodes finished in an average of 23.7382545471. Running score: 0.26


We see that expected SARSA does not perform as well as SARSA or Q-learning in terms of average reward. Like planning agents, expected sarsa also reaches the goal faster than SARSA and Q-learning (averaged of multiple 1000 episode runs)

### Double Q-learning

Double Q-learning was proposed to aleviate the positve bias induced by the max-operation in standard Q-learning.

In [8]:
import doubleQ

In [9]:
Q = doubleQ.train(env)

Episode 0 finished after 9 timesteps with r=0.0. Running score: 0.0
Episode 1 finished after 13 timesteps with r=0.0. Running score: 0.0
Episode 2 finished after 3 timesteps with r=0.0. Running score: 0.0
Episode 3 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 4 finished after 10 timesteps with r=0.0. Running score: 0.0
Episode 5 finished after 22 timesteps with r=0.0. Running score: 0.0
Episode 6 finished after 10 timesteps with r=0.0. Running score: 0.0
Episode 7 finished after 5 timesteps with r=0.0. Running score: 0.0
Episode 8 finished after 46 timesteps with r=0.0. Running score: 0.0
Episode 9 finished after 4 timesteps with r=0.0. Running score: 0.0
Episode 10 finished after 6 timesteps with r=0.0. Running score: 0.0
Episode 11 finished after 3 timesteps with r=0.0. Running score: 0.0
Episode 12 finished after 12 timesteps with r=0.0. Running score: 0.0
Episode 13 finished after 6 timesteps with r=0.0. Running score: 0.0
Episode 14 finished after 9 timesteps 

In [11]:
doubleQ.evaluate(env,Q)

1000 episodes finished in an average of 47.0012016296. Running score: 0.85


We see that double-Q learning is also able to solve this task, however performance is very similar to both SARSA and Q-learning

### Changing the Reward structure

We have seen that Planning agents and more elaborate methods like expected SARSA are not able to perform well on this task, as compared to Q-learning and SARSA. We believe that one of the reasons for this the stochasticity of the environment.

An interesting feature of both DYNA-Q and Expected SARSA is that they find solutions in far fewer timesteps. In order to see if planning would help when the agent is trying to reach the goal as fast as possible. Accordingly, we modify the reward structure of the environment such that a reward of -1 is received for every step not reaching the goal, and a reward of 100 is received for reaching the goal.

### Q-learning

In [13]:
import qlearning_v2

In [14]:
qlearning_v2.train(env,planning=False)

Episode 0 finished after 6 timesteps with r=0.0. Running score: -6.0
Episode 1 finished after 6 timesteps with r=0.0. Running score: -6.0
Episode 2 finished after 20 timesteps with r=0.0. Running score: -10.6666666667
Episode 3 finished after 16 timesteps with r=0.0. Running score: -12.0
Episode 4 finished after 10 timesteps with r=0.0. Running score: -11.6
Episode 5 finished after 4 timesteps with r=0.0. Running score: -10.3333333333
Episode 6 finished after 3 timesteps with r=0.0. Running score: -9.28571428571
Episode 7 finished after 6 timesteps with r=0.0. Running score: -8.875
Episode 8 finished after 31 timesteps with r=0.0. Running score: -11.3333333333
Episode 9 finished after 14 timesteps with r=0.0. Running score: -11.6
Episode 10 finished after 5 timesteps with r=0.0. Running score: -11.0
Episode 11 finished after 19 timesteps with r=0.0. Running score: -11.6666666667
Episode 12 finished after 12 timesteps with r=100.0. Running score: -4.0
Episode 13 finished after 17 timest

array([[ 37.46534626,  17.35560125,  14.07011967,   4.21155502],
       [  0.89721378,   0.89545727,   0.9       ,  34.04681836],
       [  4.22551017,   0.93669182,   0.92567926,  30.86400123],
       [  0.89477054,   0.89577353,   0.9       ,  29.91335797],
       [ 39.02055142,  10.45342153,   7.93442159,   4.3099443 ],
       [  1.        ,   1.        ,   1.        ,   1.        ],
       [ 17.85874716,   0.729     ,   0.77714202,   0.74569044],
       [  1.        ,   1.        ,   1.        ,   1.        ],
       [  5.28740829,   5.276618  ,   4.8606614 ,  44.49874487],
       [ 13.78856332,  48.01064869,   0.89614512,   7.14292871],
       [  2.45795849,   0.9       ,  38.49132423,   1.        ],
       [  1.        ,   1.        ,   1.        ,   1.        ],
       [  1.        ,   1.        ,   1.        ,   1.        ],
       [  5.96498699,   0.80757243,  62.40623559,   0.9       ],
       [  0.999     ,  81.93841406,   1.        ,   1.        ],
       [  1.        ,   1

In [15]:
qlearning_v2.evaluate(env,Q)

1000 episodes finished in an average of 48.8219528198. Running score: 28.41


###SARSA

In [16]:
import sarsa_v2

In [21]:
sarsa_v2.train(env,planning=False)

Episode 0 finished after 5 timesteps with r=0.0. Running score: -6.0
Episode 1 finished after 5 timesteps with r=0.0. Running score: -6.0
Episode 2 finished after 8 timesteps with r=0.0. Running score: -7.0
Episode 3 finished after 2 timesteps with r=0.0. Running score: -6.0
Episode 4 finished after 3 timesteps with r=0.0. Running score: -5.6
Episode 5 finished after 11 timesteps with r=0.0. Running score: -6.66666666667
Episode 6 finished after 7 timesteps with r=0.0. Running score: -6.85714285714
Episode 7 finished after 16 timesteps with r=0.0. Running score: -8.125
Episode 8 finished after 15 timesteps with r=0.0. Running score: -9.0
Episode 9 finished after 18 timesteps with r=100.0. Running score: 0.0
Episode 10 finished after 3 timesteps with r=0.0. Running score: -0.363636363636
Episode 11 finished after 15 timesteps with r=0.0. Running score: -1.66666666667
Episode 12 finished after 22 timesteps with r=0.0. Running score: -3.30769230769
Episode 13 finished after 14 timesteps w

array([[ 43.71183975,  36.61920346,  33.98692126,  29.98969814],
       [ 14.08176323,  11.15856726,  12.44474966,  37.8327351 ],
       [ 31.59467765,   6.10368735,  11.76034603,  10.06091498],
       [  0.9981    ,   0.99782639,   0.8991    ,  15.40128693],
       [ 46.45172029,  26.668125  ,  22.62120857,  20.69465896],
       [  1.        ,   1.        ,   1.        ,   1.        ],
       [ 24.97566345,   3.86237782,  10.51431021,   3.65650192],
       [  1.        ,   1.        ,   1.        ,   1.        ],
       [ 26.7817066 ,  11.96639084,  28.50837879,  50.63743774],
       [ 22.85041526,  54.93281707,  11.72752624,  19.91322032],
       [ 48.50746168,  15.67658989,  15.60606845,   5.62555589],
       [  1.        ,   1.        ,   1.        ,   1.        ],
       [  1.        ,   1.        ,   1.        ,   1.        ],
       [ 16.83692209,  32.58759652,  66.49892992,  15.0044698 ],
       [  7.56231305,  38.2992238 ,  76.72356788,  27.47008367],
       [  1.        ,   1

In [22]:
sarsa_v2.evaluate(env,Q)

1000 episodes finished in an average of 47.9486885071. Running score: 31.05


### DYNA-Q

In [23]:
qlearning_v2.train(env,planning=True)

Episode 0 finished after 4 timesteps with r=0.0. Running score: -4.0
Episode 1 finished after 2 timesteps with r=0.0. Running score: -3.0
Episode 2 finished after 17 timesteps with r=0.0. Running score: -7.66666666667
Episode 3 finished after 30 timesteps with r=0.0. Running score: -13.25
Episode 4 finished after 13 timesteps with r=0.0. Running score: -13.2
Episode 5 finished after 36 timesteps with r=0.0. Running score: -17.0
Episode 6 finished after 13 timesteps with r=0.0. Running score: -16.4285714286
Episode 7 finished after 41 timesteps with r=0.0. Running score: -19.5
Episode 8 finished after 49 timesteps with r=0.0. Running score: -22.7777777778
Episode 9 finished after 145 timesteps with r=0.0. Running score: -35.0
Episode 10 finished after 14 timesteps with r=0.0. Running score: -33.0909090909
Episode 11 finished after 5 timesteps with r=0.0. Running score: -30.75
Episode 12 finished after 15 timesteps with r=0.0. Running score: -29.5384615385
Episode 13 finished after 17 ti

array([[  8.11858256e-01,   1.00610206e-02,   1.07826019e+01,
          1.00592463e-02],
       [  1.00647248e-02,   1.00000000e-03,   1.00000000e-03,
          9.53243943e+00],
       [  9.60684064e-03,   1.18575125e-02,   1.10905575e+01,
          8.58777692e-03],
       [  1.00000000e-03,   1.00000000e-03,   1.00000000e-03,
          8.05715525e+00],
       [  1.30091430e+01,   1.00000000e-03,   1.00000003e-03,
          1.00000000e-03],
       [  1.00000000e+00,   1.00000000e+00,   1.00000000e+00,
          1.00000000e+00],
       [  1.00000000e-03,   1.00000000e-03,   1.54699503e+01,
          1.00000000e-03],
       [  1.00000000e+00,   1.00000000e+00,   1.00000000e+00,
          1.00000000e+00],
       [  1.00000000e-03,   1.00000000e-03,   1.00000000e-03,
          1.69266449e+01],
       [  1.84001204e-02,   3.03520209e+01,   1.00000000e-03,
          1.00000000e-03],
       [  1.17915846e-02,   2.75524159e+01,   1.00000000e-03,
          1.00000000e-03],
       [  1.00000000e

In [24]:
qlearning_v2.evaluate(env,Q)

1000 episodes finished in an average of 47.2740402222. Running score: 40.7


In the case where the reward is maxized if the agent reaches the fast as possible, we see that planning does in fact help. This is true even though the environment is stochastic. The planning agent now takes almost as long as Q-learning and SARSA, howver it achieves a larger average reward.